# Introduction to PyTorch

PyTorch is a Python package for performing tensor computation, automatic differentiation, and dynamically defining neural networks. It makes it particularly easy to accelerate model training with a GPU. In recent years it has gained a large following in the NLP community.


## Installing PyTorch

Instructions for installing PyTorch can be found on the home-page of their website: <http://pytorch.org/>. The PyTorch developers recommended you use the `conda` package manager to install the library (in my experience `pip` works fine as well).

One thing to be aware of is that the package name will be different depending on whether or not you intend on using a GPU. If you do plan on using a GPU, then you will need to install CUDA and CUDNN before installing PyTorch. Detailed instructions can be found at NVIDIA's website: <https://docs.nvidia.com/cuda/>. The following versions of CUDA are supported: 7.5, 8, and 9.


## PyTorch Basics

The PyTorch API is designed to very closely resemble NumPy. The central object for performing computation is the `Tensor`, which is PyTorch's version of NumPy's `array`.

In [9]:
import numpy as np
import torch

In [ ]:
# Create a 3 x 2 array
np.ndarray((3, 2))

In [ ]:
# Create a 3 x 2 Tensor
torch.Tensor(3, 2)

All of the basic arithmetic operations are supported.

In [ ]:
a = torch.Tensor([1,2])
b = torch.Tensor([3,4])
print('a + b:', a + b)
print('a - b:', a - b)
print('a * b:', a * b)
print('a / b:', a / b)

Indexing/slicing also behaves the same.

In [ ]:
a = torch.Tensor(5, 5)
print('a:', a)

# Slice using ranges
print('a[2:4, 3:4]', a[2:4, 3:4])

# Can count backwards using negative indices
print('a[:, -1]', a[:, -1])

# Skipping elements
print('a[::2, ::3]', a[::2, ::3])

Changing a `Tensor` to and from an `array` is also quite simple:

In [ ]:
# Tensor from array
arr = np.array([1,2])
torch.from_numpy(arr)

In [ ]:
# Tensor to array
t = torch.Tensor([1, 2])
t.numpy()

Moving `Tensor`s to the GPU is also quite simple:

In [ ]:
t = torch.Tensor([1, 2]) # on CPU
if torch.cuda.is_available():
    t = t.cuda() # on GPU

## Automatic Differentiation

Derivatives and gradients are critical to a large number of machine learning algorithms. One of the key benefits of 
PyTorch is that these can be computed automatically by `Variable` objects.

We'll demonstrate this using the following example. Suppose we have some data $x$ and $y$, and want to fit a model:
$$ \hat{y} = mx + b $$
by minimizing the loss function:
$$ L(y, \hat{y}) = \frac{1}{2}(y - \hat{y})^2 $$


In [ ]:
from torch.autograd import Variable

# Data
x = Variable(torch.Tensor([1,  2,  3,  4]))
y = Variable(torch.Tensor([0, -1, -2, -3]))

# Initialize a variables
m = Variable(torch.rand(1), requires_grad=True)
b = Variable(torch.rand(1), requires_grad=True)

# Define function
y_hat = m * x + b

# Define loss
loss = torch.mean(0.5 * (y - y_hat)**2)

To obtain the gradient of the $L$ w.r.t $m$ and $b$ you need only run:

In [ ]:
loss.backward() # Backprop the gradients of the loss w.r.t other variables

# Gradients
print('dL/dm: %0.4f' % m.grad.data)
print('dL/db: %0.4f' % b.grad.data)

## Training Models

While automatic differentiation is in itself a useful feature, it can be quite tedious to keep track of all of the different parameters and gradients for more complicated models. In order to make life simple, PyTorch defines a `torch.nn.Module` class which handles all of these details for you. To paraphrase the PyTorch documentation, this is the base class for all neural network modules, and whenever you define a model it should be a subclass of this class.

Here is an example implementation of the simple linear model given above:

In [ ]:
import torch.nn as nn

class LinearModel(nn.Module):
    
    def __init__(self):
        """This method is called when you instantiate a new LinearModel object.
        
        You should use it to define the parameters/layers of your model.
        """
        # Whenever you define a new nn.Module you should start the __init__()
        # method with the following line. Remember to replace `LinearModel` 
        # with whatever you are calling your model.
        super(LinearModel, self).__init__()
        
        # Now we define the parameters used by the model.
        self.m = torch.nn.Parameter(torch.rand(1))
        self.b = torch.nn.Parameter(torch.rand(1))
    
    def forward(self, x):
        """This method computes the output of the model.
        
        Args:
            x: The input data.
        """
        return self.m * x + self.b


# Example forward pass. Note that we use model(x) not model.forward(x) !!! 
model = LinearModel()
y_hat = model(x)

To train this model we need to pick an optimizer such as SGD, AdaDelta, ADAM, etc. There are many options in `torch.optim`. When initializing an optimizer, the first argument will be the collection of variables you want optimized. To obtain a list of all of the trainable parameters of a model you can call the `nn.Module.parameters()` method. For example, the following code initalizes a SGD optimizer for the model defined above:

In [ ]:
import torch.optim as optim
optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)

Training is done in a loop. The general structure is:

1. Clear the gradients.
2. Evaluate the model.
3. Calculate the loss.
4. Backpropagate.
5. Perform an optimization step.
6. (Once in a while) Print monitoring metrics.

For example, we can train our linear model by running:

In [ ]:
import time

for i in range(5001):
    optimizer.zero_grad()
    y_hat = model(x)
    loss = torch.mean(0.5 * (y - y_hat)**2)
    loss.backward()
    optimizer.step()
    if i % 1000 == 0:
        time.sleep(1) # DO NOT INCLUDE THIS IN YOUR CODE !!! Only for demo.
        print(f'Iteration {i} - Loss: {loss.item():0.6f}', end='\r')

Observe that the final parameters are what we expect:

In [ ]:
print('Final parameters:')
print('m: %0.2f' % model.m)
print('b: %0.2f' % model.b)

# CASE STUDY: Word2Vec

Now let's dive into an example that is more relevant to NLP, Word2Vec!
The idea of Word2Vec is to create continuous vector representations of words using shallow neural networks, so that words with similar meanings end up close together in the vector space.
First introduced by [Mikolov et. al 2013](https://arxiv.org/abs/1301.3781), these models greatly improved the state-of-the-art of measuring semantic and syntactic similarity of words.
In addition, the learned word embeddings end up being useful for many other downstream tasks such as language modeling, machine translation, and automatic image captioning.

In this notebook, we will go over the continuous bag-of-words (CBOW) model, which has the following architecture:
![Mikolov et. al](img/cbow.png)
Given a word $w_i$ in our corpus as well as a context $c = [w_{i-k}, \ldots,w_{i-1}, w_{i+1}, w_{i+k}]$ comprised of words in a window of size $k$ around $w_i$ the goal is to maximize $p(W_i = w_i | c)$. In the CBOW model this is done by:
1. Embedding the context words $w_{i+j}$  into a lower dimensional space to get word vectors $v_{i+j}$.
2. Summing up these word vectors to get $v = \sum_{j \in [-k, k]-{0}}v_{i+j}$
3. Feeding $v$ into a fully connected layer with softmax activation to obtain the output probabilities. That is, $P(w_i | c) = \text{softmax}(Av + b)$.

Since the output is a probability distribution over a categorical variable we will use cross-entropy as our loss function.

## Dataset

To start, we'll need some data to train on. We will use the text8 dataset since it does not require tokenization (the tokens can be obtained by splitting the document on spaces). The dataset can be downloaded by running the following shell scripts:

In [3]:
!wget http://mattmahoney.net/dc/text8.zip
!unzip text8.zip

--2020-01-29 20:25:13--  http://mattmahoney.net/dc/text8.zip
Resolving mattmahoney.net (mattmahoney.net)... 67.195.197.75
Connecting to mattmahoney.net (mattmahoney.net)|67.195.197.75|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 31344016 (30M) [application/zip]
Saving to: ‘text8.zip.2’

text8.zip.2           8%[>                   ]   2.65M   826KB/s    eta 34s    ^C
^C


In [4]:
with open('text8', 'r') as f:
    corpus = f.read().split()

Next, we need to get our data into Python and in a form that is usable by PyTorch. For text data this typically entails building a vocabulary of all of the words, sorting the vocabulary in terms of frequency, and then mapping words to integers corresponding to their place in the sorted vocabulary. This can be done as follows:

In [5]:
from collections import Counter


def build_vocabulary(corpus):
    """Builds a vocabulary.
    
    Args:
        corpus: A list of words.
    """
    counts = Counter(corpus) # Count the word occurances.
    counts = counts.items() # Transform Counter to (word, count) tuples.
    counts = sorted(counts, key=lambda x: x[1], reverse=True) # Sort in terms of frequency.
    reverse_vocab = [x[0] for x in counts] # Use a list to map indices to words.
    vocab = {x: i for i, x in enumerate(reverse_vocab)} # Invert that mapping to get the vocabulary.
    data = [vocab[x] for x in corpus] # Get ids for all words in the corpus.
    return data, vocab, reverse_vocab


data, vocab, reverse_vocab = build_vocabulary(corpus)

Use the following cell to inspect the output of that function.

In [ ]:
reverse_vocab[data[0]]

We now need a function to generate batches of word-context pairs from the corpus.

In [6]:
from collections import deque
from random import shuffle
from torch.autograd import Variable


def batch_generator(data, batch_size, window_size):

    # Stores the indices of the words in order that they will be chosen when generating batches.
    # e.g. the first word that will be chosen in an epoch is word_ids[0]
    ids = list(range(window_size, len(data) - window_size))

    while True:
        shuffle(ids) # Randomize at the start of each epoch
        sample_queue = deque()
        for id in ids: # Iterate over random words
            w = data[id]
            c = []
            for i in range(1, window_size + 1): # Iterate over window sizes
                c.append(data[id - i]) # Left context
                c.append(data[id + i]) # Right context
            sample_queue.append((w, c))
            
            # Once positive sample queue is full deque a batch and generate negative samples
            if len(sample_queue) >= batch_size:
                
                batch = [sample_queue.pop() for _ in range(batch_size)]
                w, c = zip(*batch) # Separate words and contexts
                
                # Read data into torch variables
                w = Variable(torch.LongTensor(w))
                c = Variable(torch.LongTensor(c))
                
                # Transfer data to GPU if available
                if torch.cuda.is_available():
                    w = w.cuda()
                    c = c.cuda()
                    
                yield w, c

Here's an example of the `batch_generator` in action...

In [10]:
# Training hyperparameters
batch_size = 4
window_size = 1

# Example usage
it = batch_generator(data, batch_size, window_size) # Initialize the iterable
w, c = next(it) # The next() function will run until yield
print('w:', w)
print('c:', c)

w: tensor([ 5849,  2160, 28342,     3], device='cuda:0')
c: tensor([[  1,   4],
        [519,   1],
        [290, 118],
        [ 16,   6]], device='cuda:0')


## Model

Now that we can read in the data, it is time to build our model. Note that the code almost perfectly follows the mathematical description of CBOW given above. However there are a few noteworthy differences:
1. In the `__init__` method we also include code to initialize the embedding weights using a uniform distribution.
    This is a standard practice when training embeddings.
2. Instead of outputting probabilities the `forward` method outputs log probabilities.
    This is the expected input for the negative log likelihood loss function we will use during training.

In [7]:
import torch.nn as nn
import torch.nn.functional as F


class CBOW(nn.Module):
    
    def __init__(self, vocab_size, embedding_size):
        super(CBOW, self).__init__()
        # Parameters
        self.vocab_size = vocab_size
        self.embedding_size = embedding_size
        # Layers
        self.embeddings = nn.Embedding(vocab_size, embedding_size)
        self.fc = nn.Linear(embedding_size, vocab_size)
        # Initialize embedding weights
        initrange = 0.5 / embedding_size
        self.embeddings.weight.data.uniform_(-initrange, initrange)
    
    def forward(self, c):
        batch_size, window_size = c.size()
        net = c.view(-1) # Flatten window dimension
        net = self.embeddings(net) # Get context embeddings
        net = net.view(batch_size, window_size, self.embedding_size) # Unflatten window dimension
        net = torch.sum(net, dim=1) # Sum over window dimension
        net = self.fc(net) # Feed into fully-connected layer
        net = F.log_softmax(net, dim=1) # Log probabilities
        return net

## Training

The training script essentially follows the same pattern that we used for the linear model above. The only change is that we have added a batch generation step to the start of the training loop.

In [23]:
from torch import optim

# Training settings / hyperparameters
n_iterations = 10000
batch_size = 64
window_size = 10
it = batch_generator(data, batch_size, window_size)

vocab_size = len(vocab)
embedding_size = 64
model = CBOW(vocab_size, embedding_size)
if torch.cuda.is_available():
    model = model.cuda()

loss_function = nn.NLLLoss()
optimizer = optim.Adam(model.parameters())

for i in range(n_iterations):
    w, c = next(it) # Generate a new batch of data
    optimizer.zero_grad()
    output = model(c)
    loss = loss_function(output, w)
    loss.backward()
    optimizer.step()
    # if (i % 100) == 0:
    print('Iteration %i - Loss: %0.6f' % (i, loss.item()), end='\r')

KeyboardInterrupt: 

## Saving and Loading Trained Models

When you are finished training, saving your model is as easy as:

In [15]:
torch.save(model.state_dict(), 'model.pt')

and loading is similarly easy:

In [16]:
state_dict = torch.load('model.pt')
model.load_state_dict(state_dict)

<All keys matched successfully>

## Fun with Word Vectors

Time for some fun word vector examples. To start we will need to extract our word embeddings from the model. We'll then read them into NumPy arrays so they can be used by SciPy, scikit-learn, etc.

In [24]:
# Extract the embedding weights from the model
embeddings = model.embeddings.weight.data

# Transform the weight tensor to a numpy array
if torch.cuda.is_available():
    embeddings = embeddings.cpu().numpy()
else:
    embeddings = embeddings.numpy()

One interesting visual is to look at a t-SNE plot of the word vectors:

In [26]:
import matplotlib.pyplot as plt
from sklearn.manifold import TSNE

# Get the t-SNE embeddings.
tsne = TSNE(n_components=2).fit_transform(embeddings[:2000])

# Create a scatter plot
fig = plt.figure(figsize=(12, 12), dpi=900)
ax = fig.add_subplot(111)
ax.scatter(tsne[:,0], tsne[:,1])

# Randomly select some words and label them
random_choices = np.random.choice(2000, 100, replace=False)
for i in random_choices:
    ax.text(tsne[i, 0], tsne[i, 1], reverse_vocab[i], fontsize=12, color='black')

Another fun application is to find similar words using cosine distance:

In [27]:
import scipy

def similar_words(word,
                  embeddings=embeddings,
                  vocab=vocab,
                  reverse_vocab=reverse_vocab):
    print('Most similar words to: %s' % word)
    # Get embedding for query word.
    word_idx = vocab[word]
    input_embedding = embeddings[word_idx:word_idx+1, :]
    # Compute cosine distance between query word embedding and all other embeddings.
    cosine_distance = scipy.spatial.distance.cdist(input_embedding, embeddings, 'cosine')
    # Find closest embeddings and print out corresponding words.
    closest_word_ids = np.argsort(cosine_distance)[0][1:11]
    for i, close_word_idx in enumerate(closest_word_ids):
        print('%i - %s' % (i + 1, reverse_vocab[close_word_idx]))

In [28]:
similar_words('chaos')

Most similar words to: chaos
1 - sadly
2 - crosswise
3 - anjou
4 - comprehend
5 - batmobile
6 - sarris
7 - chameleon
8 - manifested
9 - arranged
10 - domestication


In [29]:
similar_words('business', embeddings[:2000])

Most similar words to: business
1 - units
2 - study
3 - account
4 - opened
5 - scientists
6 - introduction
7 - percent
8 - spent
9 - interpretation
10 - composed
